In [9]:
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

# Define the base model ID
base_model_id = "meta-llama/Llama-2-13b-hf"

# Create a BitsAndBytesConfig object with the corrected settings
quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
    load_in_8bit_fp32_cpu_offload=True  # Set as suggested in the error
)

# Load the base model with the updated quantization configuration
# Adjust 'device_map' based on your system's GPU configuration
base_model = AutoModelForCausalLM.from_pretrained(
    base_model_id,  
    quantization_config=quantization_config,
    trust_remote_code=True,
    use_auth_token=True
)

# Load the tokenizer
tokenizer = AutoTokenizer.from_pretrained(base_model_id, add_bos_token=True, trust_remote_code=True)


/home/z/miniconda3/envs/llama/lib/python3.10/site-packages/transformers/models/auto/auto_factory.py:472: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

/home/z/miniconda3/envs/llama/lib/python3.10/site-packages/transformers/utils/hub.py:374: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


Now load the QLoRA adapter from the appropriate checkpoint directory, i.e. the best performing model checkpoint:

In [10]:
from peft import PeftModel

ft_model = PeftModel.from_pretrained(base_model, "checkpoint-2800")

In [11]:
from datasets import load_dataset

  
eval_dataset = load_dataset('json', data_files='/home/z/Music/LLAMA/llama/IPG/datasets/new_test_data.json', split='train')


def formatting_func(example):
    text = f"### The job description: {example['text']}\n ### The skills: "
    return text



In [12]:


def run_finetune_model(model_id):

    example = eval_dataset.filter(lambda x: x['id'] == model_id)[0]
    formatted_text = formatting_func(example)
    
    #print(formatted_text)
    model_input = tokenizer(formatted_text, return_tensors="pt").to("cuda")


    ft_model.eval()
    with torch.no_grad():
        output_tokens = ft_model.generate(**model_input, max_new_tokens=200)[0]
        generated_text = tokenizer.decode(output_tokens, skip_special_tokens=True)
    
    print(generated_text)




In [13]:
run_finetune_model("19010")


### The job description: German BD Manager
Job Description：
1、Represent the company to develop new partners for energy storage system；
2、Maintain good relationship and help partners to develop/grow the business；
3、Formulate a strategy and target for the market exploration so as to achieve good performance；
4、Pay attention and collect information for the latest development/tendency in the industry as well as getting feedback/insight to R&D；
5、Advice and assist the company to build a strong local team including but not limited to after sale service, technical support, sales and marketing.
 
Job Requirements：
1、Fluent in English and German；
2、5+ years of experience in the industry of Energy Storage System, a good education background will be preferential；
3、Strong execution and result-oriented, attach importance to details and critical thinking as well as desire to progress/evolve；
4、Open-minded and teamwork, great skills in communication.
 ### The skills:  ['programming', 'simulation', '